<a href="https://colab.research.google.com/github/hududed/mlr3mbo-demo/blob/main/multiobjective_visualization.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!apt-get update
!apt install -y xvfb firefox
!pip install selenium

# Download and install geckodriver
!wget https://github.com/mozilla/geckodriver/releases/download/v0.34.0/geckodriver-v0.34.0-linux64.tar.gz
!tar -xvzf geckodriver-v0.34.0-linux64.tar.gz
!chmod +x geckodriver
!mv geckodriver /usr/local/bin/

!git clone https://github.com/hududed/mlr3mbo-demo
!mv mlr3mbo-demo/ mlr3mbo_demo

Get:1 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease [3,626 B]
Get:2 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  InRelease [1,581 B]
Hit:3 https://ppa.launchpadcontent.net/c2d4u.team/c2d4u4.0+/ubuntu jammy InRelease
Hit:4 http://archive.ubuntu.com/ubuntu jammy InRelease
Get:5 http://security.ubuntu.com/ubuntu jammy-security InRelease [110 kB]
Hit:6 https://ppa.launchpadcontent.net/deadsnakes/ppa/ubuntu jammy InRelease
Hit:7 https://ppa.launchpadcontent.net/graphics-drivers/ppa/ubuntu jammy InRelease
Hit:8 https://ppa.launchpadcontent.net/ubuntugis/ppa/ubuntu jammy InRelease
Get:9 http://archive.ubuntu.com/ubuntu jammy-updates InRelease [119 kB]
Get:10 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  Packages [673 kB]
Get:11 http://archive.ubuntu.com/ubuntu jammy-backports InRelease [109 kB]
Get:12 http://security.ubuntu.com/ubuntu jammy-security/main amd64 Packages [1,440 kB]
Get:13 http://archive.ubuntu.c

In [2]:
from bokeh.models import LinearColorMapper
from bokeh.models import (
    ColumnDataSource,
    LinearColorMapper,
)
from mlr3mbo_demo.visualization.data_processing import (
    read_data,
    perform_pca,
    define_grid,
    interpolate_data,
    create_weighted_sum,
    clean_column_names
)
from mlr3mbo_demo.visualization.plotting import (
    create_hover_tool,
    create_figure,
    add_image_glyph,
    add_circle_glyph,
    add_color_bar,
    show_figure,
    save_figure,
)
import numpy as np

# Read the data
# BE SURE TO ADD THE DATA FILE `CuAlMnNi-data.csv` in the left file / folder pane
data = read_data("CuAlMnNi-data.csv")
print(data.columns)

data = clean_column_names(data)

print(data.columns)


Index(['Sample #', 'Cu (at%)', 'Al (at%)', 'Mn (at%)', 'Ni (at%)',
       'Enthalpy (J/g)', 'DSC Ms (°C)', 'DSC Mf (°C)', 'DSC As (°C)',
       'DSC Af (°C)', 'Thermal Hysteresis (°C)'],
      dtype='object')
Index(['sample_number', 'cu_at_percent', 'al_at_percent', 'mn_at_percent',
       'ni_at_percent', 'enthalpy_j_per_g', 'dsc_ms_c', 'dsc_mf_c', 'dsc_as_c',
       'dsc_af_c', 'thermal_hysteresis_c'],
      dtype='object')


In [3]:
# Perform PCA
data = perform_pca(
    data, ["cu_at_percent", "al_at_percent", "mn_at_percent", "ni_at_percent"]
)

# Define the grid
x = np.linspace(data["PC1"].min(), data["PC1"].max(), 500)
y = np.linspace(data["PC2"].min(), data["PC2"].max(), 500)
x_grid, y_grid = define_grid(data, 500)

# Interpolate the DSC Af values
z1 = interpolate_data(data, x_grid, y_grid, "dsc_af_c")

# Interpolate the Enthalpy values
z2 = interpolate_data(data, x_grid, y_grid, "enthalpy_j_per_g")

# Create a weighted sum of the "dsc_af_c" and "enthalpy_j_per_g" columns
data = create_weighted_sum(data, 0.5, 0.5, "dsc_af_c", "enthalpy_j_per_g")

# Interpolate the weighted sum values
z4 = interpolate_data(data, x_grid, y_grid, "Weighted Sum")

# Create a color mapper for DSC Af
color_mapper1 = LinearColorMapper(
    palette="Viridis256",
    low=np.min(z1[z1 > -9999]),
    high=np.max(z1[z1 > -9999]),
    nan_color="white",
)

# Create a color mapper for Enthalpy
color_mapper2 = LinearColorMapper(
    palette="Inferno256",
    low=np.min(z2[z2 > -9999]),
    high=np.max(z2[z2 > -9999]),
    nan_color="white",
)

color_mapper4 = LinearColorMapper(
    palette="Turbo256",
    low=np.min(z4[z4 > -9999]),
    high=np.max(z4[z4 > -9999]),
    nan_color="white",
)

# Create a ColumnDataSource from data
source = ColumnDataSource(data)

# Create a hover tool
hover = create_hover_tool(
    [
        ("Cu", "@cu_at_percent"),
        ("Al", "@al_at_percent"),
        ("Mn", "@mn_at_percent"),
        ("Ni", "@ni_at_percent"),
        ("DSC Af", "@dsc_af_c"),
        ("Enthalpy", "@enthalpy_j_per_g"),
    ]
)

# Create a new plot for DSC Af
p1 = create_figure(
    hover, (x.min(), x.max()), (y.min(), y.max()), "PCA and Interpolation of DSC Af"
)


# Add the image glyph for DSC Af
add_image_glyph(
    p1,
    [z1],
    (x.min(), x.max()),
    (y.min(), y.max()),
    color_mapper1,
    "Interpolated DSC Af",
)

# Add a circle renderer with vectorized colors and sizes and a legend
add_circle_glyph(p1, source, "Data Points")
# Add a color bar for DSC Af
add_color_bar(p1, color_mapper1)

# Show the plot
show_figure(p1)

# Save the plots as PNG images
save_figure(p1, "DSC_Af.png")

# Repeat the process for the other plots
p2 = create_figure(
    hover, (x.min(), x.max()), (y.min(), y.max()), "PCA and Interpolation of Enthalpy"
)
add_image_glyph(
    p2,
    [z2],
    (x.min(), x.max()),
    (y.min(), y.max()),
    color_mapper2,
    "Interpolated Enthalpy",
)
add_circle_glyph(p2, source, "Data Points")
add_color_bar(p2, color_mapper2)
show_figure(p2)
save_figure(p2, "Enthalpy.png")

p4 = create_figure(
    hover,
    (x.min(), x.max()),
    (y.min(), y.max()),
    "PCA and Interpolation of Weighted Sum",
)
add_image_glyph(
    p4,
    [z4],
    (x.min(), x.max()),
    (y.min(), y.max()),
    color_mapper4,
    "Interpolated Weighted Sum",
)
add_circle_glyph(p4, source, "Data Points")
add_color_bar(p4, color_mapper4)
show_figure(p4)
save_figure(p4, "Weighted.png")